In [ ]:
import os
import shapefile
import mapbox_vector_tile
from mapbox_vector_tile.encoder import on_invalid_geometry_make_valid
import mercantile

from shapely.ops import transform
from shapely import affinity 
from shapely.geometry import shape, mapping, Polygon, MultiPolygon, LinearRing, LineString, MultiLineString
from shapely.geometry.polygon import orient

import pyproj
from collections import defaultdict

import pandas as pd
import subprocess

In [ ]:

projectTo4326 = pyproj.Transformer.from_crs(
    pyproj.CRS('EPSG:3857'),  # 소스 좌표계
    pyproj.CRS('EPSG:4326'),  # 소스 좌표계
    always_xy=True
).transform

# 타일 경계 설정 및 변환 함수
def transform_coords(x, y, bounds, _MVT_EXTENT):
    x = int((x - bounds.left) / (bounds.right - bounds.left) * _MVT_EXTENT)
    y = int((y - bounds.bottom) / (bounds.top - bounds.bottom) * _MVT_EXTENT)
    return (x, y)

def transform_polygon(polygon, bounds, _MVT_EXTENT):
    exterior_coords = [transform_coords(x, y, bounds, _MVT_EXTENT) for x, y in zip(*polygon.exterior.xy)]
    interiors = [LinearRing([transform_coords(x, y, bounds, _MVT_EXTENT) for x, y in zip(*interior.xy)]) for interior in polygon.interiors]
    return Polygon(exterior_coords, interiors)

def transform_linestring(linestring, bounds, _MVT_EXTENT):
    coords = [transform_coords(x, y, bounds, _MVT_EXTENT) for x, y in zip(*linestring.xy)]
    return LineString(coords)

def transform_multilinestring(multilinestring, bounds, _MVT_EXTENT):
    lines = [transform_linestring(linestring, bounds, _MVT_EXTENT) for linestring in multilinestring.geoms]
    return MultiLineString(lines)


def orient_geometry(geom, sign=1.0):
    """
    주어진 지오메트리(폴리곤 또는 멀티폴리곤)를 올바르게 정렬합니다.
    외부 링은 반시계방향, 내부 링(구멍)은 시계방향으로 설정합니다.
    """
    if isinstance(geom, Polygon):
        return orient(geom, sign)  # 단일 폴리곤 정렬
    elif isinstance(geom, MultiPolygon):
        oriented_polygons = [orient(p, sign) for p in geom.geoms]
        return MultiPolygon(oriented_polygons)  # 멀티폴리곤 정렬
    else:
        raise ValueError("Unsupported geometry type")

def orient_shapes_in_shapefile(shapes, sign=1.0):
    """
    Shapefile에서 읽은 지오메트리 리스트를 정렬하여 반환합니다.
    """
    oriented_shapes = []
    for geom in shapes:
        oriented_shape = orient_geometry(geom, sign)
        oriented_shapes.append(oriented_shape)
    return oriented_shapes


def read_and_transform_shapefile(filename, source_crs_manual='EPSG:3857', target_crs='EPSG:3857'):
    # Shapefile 읽기
    sf_raw = shapefile.Reader(filename)

    # 좌표계 정보 읽기
    # .prj 파일이 있는 경우 이를 읽어서 좌표계 확인
    prj_filename = filename.replace('.shp', '.prj')
    source_crs = None

    try:
        with open(prj_filename, 'r') as prj_file:
            prj_text = prj_file.read()
            source_crs = pyproj.CRS.from_wkt(prj_text)
    except FileNotFoundError:
            print(f"No .prj file found for {filename}. Using manual source CRS.")
            print(f"Manual source CRS: {source_crs_manual}")
            source_crs = pyproj.CRS.from_string(source_crs_manual)

    # 타겟 좌표계 설정
    target_crs = pyproj.CRS(target_crs)

    # 좌표 변환 설정
    if source_crs is not None and source_crs != target_crs:
        transformer = pyproj.Transformer.from_crs(source_crs, target_crs, always_xy=True).transform
        # shape 컬렉션 가져오기 및 좌표 변환 적용

        shape_records = [(transform(transformer, shape(s.__geo_interface__)), sr.record.as_dict()) \
                         for s, sr in zip(sf_raw.shapes(), sf_raw.shapeRecords())]
    else:
        print("Source CRS is same as target CRS or source CRS is unknown. No transformation applied.")
        shape_records = [(shape(s.__geo_interface__), sr.record.as_dict()) \
                        for s, sr in zip(sf_raw.shapes(), sf_raw.shapeRecords())]

    print(f"Read {len(shape_records)} shapes from {filename}")

    return shape_records


def run_mapshaper_command(command):
    print(f"Running command: {' '.join(command)}")
    subprocess.run(command, check=True)

def simplify_with_mapshaper(input_file, output_file, simplification_ratio,  write_fields=[], \
                             read_encoding='utf8', write_encoding='utf8'):
    mapshaper_path = os.path.join('./', 'node_modules', 'mapshaper', 'bin', 'mapshaper')
    output_file_normalized = output_file.replace('\\', '/')
    # mapshaper 명령어를 사용하여 데이터 단순화    
    # mapshaper 명령어 경로 지정
    # npm install mapshaper 필요함
    command = [
            'node', mapshaper_path, input_file,
            #'-encoding', read_encoding,  # 읽기 시 인코딩 옵션
            '-simplify', str(simplification_ratio),
            '-clean'
    ]

    # write_fields가 비어 있지 않으면 해당 필드만 남기도록 필터 추가
    if write_fields:
        fields = ','.join(write_fields)
        command.extend(['-filter-fields', fields])
    print("write_name : ", output_file_normalized)
    # 출력 파일 지정
    command.extend(['-o', output_file_normalized, f'encoding={write_encoding}'])

    run_mapshaper_command(command)

def dissolve_with_mapshaper(input_file, output_file, dissolve_fields):
    mapshaper_path = os.path.join('./', 'node_modules', 'mapshaper', 'bin', 'mapshaper')

    dissolve_command = [
        'node', mapshaper_path, input_file,
        '-dissolve', ','.join(dissolve_fields),
         '-clean',
        '-o', output_file
    ]
    run_mapshaper_command(dissolve_command)


def tile_size_at_zoom(zoom_level):
    # 지구의 둘레 (미터 단위)
    earth_circumference = 40075016.68558    
    # 줌 레벨에서 타일의 수
    num_tiles = 2 ** zoom_level    
    # 줌 레벨에서 타일 한 장의 크기 (미터 단위)
    tile_size = earth_circumference / num_tiles    
    return tile_size

def calculate_tile_cut_buffer(zoom_level, _MVT_EXTENT):

    tile_size = tile_size_at_zoom(zoom_level)
    tile_pixel = tile_size / _MVT_EXTENT
    buffer = tile_pixel * (_MVT_EXTENT * 0.03)
    return buffer


### 폴리곤 변환 함수 정의

In [ ]:


def process_polygon_layer(layer_name, folder_name, zoom_levels,  tiles_data,\
                           _MVT_EXTENT = 4096, isIncludingPolygon=True, isIncludingLines=False,\
                            source_crs_manual = "EPSG:3857"):

    # zoom_levels를 하나씩 순회
    for zoom_level in zoom_levels:

        # 사용 예제
        filename = f"{folder_name}/{layer_name}_{zoom_level}.shp"
        shape_records  = read_and_transform_shapefile(filename, source_crs_manual)
        print(f"Processing zoom level {zoom_level}, {filename}...")

        buf = calculate_tile_cut_buffer(zoom_level, _MVT_EXTENT)
        # simplified_shapes를 하나씩 순회
        for geom, record in shape_records : 

            bounds = geom.bounds
            #print(bounds)
            min_tile = mercantile.tile(*projectTo4326(bounds[0], bounds[3]), zoom_level)
            max_tile = mercantile.tile(*projectTo4326(bounds[2], bounds[1]), zoom_level)
            #print(min_tile)
            #print(max_tile)
            # min_tile부터 max_tile까지 순회
            for x_tile in range(min_tile.x, max_tile.x + 1):
                for y_tile in range(min_tile.y, max_tile.y + 1):
                    bounds = mercantile.xy_bounds(x_tile, y_tile, zoom_level)
                    
                    tile_box = Polygon([
                        (bounds.left-buf, bounds.bottom-buf),
                        (bounds.left-buf, bounds.top+buf),
                        (bounds.right+buf, bounds.top+buf),
                        (bounds.right+buf, bounds.bottom-buf),
                        (bounds.left-buf, bounds.bottom-buf)
                    ])

                    # geom과 tile_box의 교집합 계산
                    intersection = tile_box.intersection(geom)

                    if intersection.is_empty:      
                        continue                    

                    transformed_polygon = affinity.translate(intersection, xoff=-bounds.left, yoff=-bounds.bottom)
                    transformed_polygon = affinity.scale(transformed_polygon,
                         xfact=_MVT_EXTENT/(bounds.right-bounds.left), yfact=_MVT_EXTENT/(bounds.top-bounds.bottom),
                         origin=(0, 0, 0))                   

                       
                    if (isIncludingPolygon) :
                        # tile_geom을 WKT 형식의 문자열로 변환
                        serialized_geom = {
                            "geometry": transformed_polygon,
                            "properties": record,
                        }

                        # tiles_data에 저장
                        tiles_data[zoom_level][(x_tile, y_tile)][layer_name].append(serialized_geom)                   


                    if (isIncludingLines) :
                        if isinstance(intersection, Polygon):
                            exterior_coords = transformed_polygon.exterior.coords
                            interior_coords = [interior.coords for interior in transformed_polygon.interiors]

                            exterior_line = LineString(exterior_coords)
                            if interior_coords:
                                interior_lines = [LineString(coords) for coords in interior_coords]
                                transformed_linestring = MultiLineString([exterior_line] + interior_lines)
                            else:
                                transformed_linestring = exterior_line

                        elif isinstance(intersection, MultiPolygon):  
                            exterior_lines = [LineString(p.exterior.coords) for p in transformed_polygon.geoms]
                            interior_lines = [LineString(interior.coords) for p in transformed_polygon.geoms for interior in p.interiors]

                            if interior_lines:
                                transformed_linestring = MultiLineString(exterior_lines + interior_lines)
                            else:
                                transformed_linestring = MultiLineString(exterior_lines)

                        serialized_linestring = {
                            "geometry": transformed_linestring,
                            "properties": record,
                        }

                        tiles_data[zoom_level][(x_tile, y_tile)][f'{layer_name}_line'].append(serialized_linestring)
    #return tiles_data
    

## 라인 변환 함수 정의

In [ ]:

def process_lineString_layer(layer_name, folder_name, zoom_levels, tiles_data, _MVT_EXTENT):
        
    # zoom_levels를 하나씩 순회
    for zoom_level in zoom_levels:

        # 사용 예제
        filename = f"{folder_name}/{layer_name}_{zoom_level}.shp"
        shape_records  = read_and_transform_shapefile(filename)
        print(f"Processing zoom level {zoom_level}, {filename}...")

        buf =0
        # simplified_shapes를 하나씩 순회
            
        for geom, record in shape_records : 

            bounds = geom.bounds
            #print(bounds)
            min_tile = mercantile.tile(*projectTo4326(bounds[0], bounds[3]), zoom_level)
            max_tile = mercantile.tile(*projectTo4326(bounds[2], bounds[1]), zoom_level)

            # min_tile부터 max_tile까지 순회
            for x_tile in range(min_tile.x, max_tile.x + 1):
                for y_tile in range(min_tile.y, max_tile.y + 1):
                    bounds = mercantile.xy_bounds(x_tile, y_tile, zoom_level)
                    
                    tile_box = Polygon([
                        (bounds.left-buf, bounds.bottom-buf),
                        (bounds.left-buf, bounds.top+buf),
                        (bounds.right+buf, bounds.top+buf),
                        (bounds.right+buf, bounds.bottom-buf),
                        (bounds.left-buf, bounds.bottom-buf)
                    ])

                    # geom과 tile_box의 교집합 계산
                    intersection = tile_box.intersection(geom)

                    if intersection.is_empty:      
                        continue                    
                    
                    transformed = affinity.translate(intersection, xoff=-bounds.left, yoff=-bounds.bottom)
                    transformed = affinity.scale(transformed, 
                            xfact=_MVT_EXTENT/(bounds.right-bounds.left),
                            yfact=_MVT_EXTENT/(bounds.top-bounds.bottom),
                            origin=(0, 0, 0))                    

                    serialized_linestring = {
                        "geometry": transformed,
                        "properties": record,
                    }

                    tiles_data[zoom_level][(x_tile, y_tile)][f'{layer_name}'].append(serialized_linestring)
    


## 포인트 파일 변환 함수 정의

In [ ]:


def process_point_layer(layer_name, filename, zoom_level, xcol, ycol,  sourceCRS, _MVT_EXTENT, tiles_data): 
    # 파일 읽기
    df = pd.read_csv(filename, delimiter='\t')
    print("df 읽음!!")

    # 좌표 변환기 설정
    transformer = pyproj.Transformer.from_crs(sourceCRS, "EPSG:3857", always_xy=True)
        
    # 좌표 변환 수행
    transformed_coords = df.apply(lambda row: transformer.transform(row[xcol], row[ycol]), axis=1)
        
    # 변환된 좌표를 새로운 컬럼에 저장
    df['x_3857'], df['y_3857'] = zip(*transformed_coords)

    # 좌표 변환기 설정 (EPSG:3857 -> EPSG:4326)
    transformer_to_4326 = pyproj.Transformer.from_crs("EPSG:3857", "EPSG:4326", always_xy=True)

    # 좌표 변환 수행 (EPSG:3857 -> EPSG:4326)
    transformed_coords_4326 = df.apply(lambda row: transformer_to_4326.transform(row['x_3857'], row['y_3857']), axis=1)

    # 변환된 좌표를 새로운 컬럼에 저장 (EPSG:4326)
    df['lon'], df['lat'] = zip(*transformed_coords_4326)

    tiles = df.apply(lambda row: mercantile.tile(row['lon'], row['lat'], zoom_level), axis=1)
        
    # 타일 번호를 새로운 컬럼에 저장
    df['tile_x'] = tiles.apply(lambda t: t.x)
    df['tile_y'] = tiles.apply(lambda t: t.y)
    df['tile_z'] = zoom_level  # 줌 레벨은 동일하므로 하나의 컬럼으로 저장


    # 타일 경계값 계산 및 저장
    bounds = tiles.apply(lambda t: mercantile.xy_bounds(t))

    df['bnd_left'] = bounds.apply(lambda b: b[0])
    df['bnd_right'] = bounds.apply(lambda b: b[2])
    df['bnd_bottom'] = bounds.apply(lambda b: b[1])
    df['bnd_top'] = bounds.apply(lambda b: b[3])



    # 변환된 좌표 계산 및 저장
    df['x_transformed'] = ((df['x_3857'] - df['bnd_left']) / (df['bnd_right'] - df['bnd_left']) * _MVT_EXTENT).astype(int)
    df['y_transformed'] = ((df['y_3857'] - df['bnd_bottom']) / (df['bnd_top'] - df['bnd_bottom']) * _MVT_EXTENT).astype(int)

    #변환된 좌표를 WKT 형식의 문자열로 저장
    df['geometry'] = df.apply(lambda row: f"POINT ({row['x_transformed']} {row['y_transformed']})", axis=1)


    # 필요한 컬럼 제외한 속성만 남기기
    properties_cols = df.columns.difference(['x_3857', 'y_3857', 'tile_x', 'tile_y', 'tile_z', 'bnd_left', 'bnd_right', 'bnd_top', 'bnd_bottom', 'x_transformed', 'y_transformed', 'geometry'])

    # 타일 번호로 데이터 그룹핑
    grouped = df.groupby(['tile_z', 'tile_x', 'tile_y'])

    print("처리 완료. 변수에 저장 시작")
    for (z, x, y), group in grouped:
        if z not in tiles_data:
            tiles_data[z] = {}
        if (x, y) not in tiles_data[z]:
            tiles_data[z][(x, y)] = {}
        tiles_data[z][(x, y)][layer_name] = [{
            "geometry": row['geometry'],
            "properties": row[properties_cols].to_dict()
        } for _, row in group.iterrows()]
    
    print("끝")


## 전처리 전처리 전처리 전처리


## 라인 레이어 단순화

In [ ]:

#라인 자체 길이를 기준으로 전처리한다.
def filter_lines_by_length(simplified_file, output_file, limit_length):
    # Shapefile 읽기
    reader = shapefile.Reader(simplified_file)
    writer = shapefile.Writer(output_file)
    writer.fields = reader.fields[1:]  # 삭제 플래그 필드를 제외한 나머지 필드를 복사

    for sr in reader.iterShapeRecords():
        geom = shape(sr.shape.__geo_interface__)
        if isinstance(geom, MultiLineString):
            filtered_lines = [line for line in geom.geoms if line.length > limit_length]
            if filtered_lines:
                filtered_geom = MultiLineString(filtered_lines)
                if filtered_geom.length > limit_length:
                    writer.shape(mapping(filtered_geom))
                    writer.record(*sr.record)
        elif isinstance(geom, LineString) and geom.length > limit_length:
            writer.shape(mapping(geom))
            writer.record(*sr.record)

    writer.close()
    
def simplify_linestring(input_file, temp_folder, output_folder, \
                        layer_name, min_zoom, max_zoom):

    for zoom_level in range(min_zoom, max_zoom+1):
        simplified_file = os.path.join(temp_folder, f"{layer_name}_{zoom_level}.shp")
        simplification_ratio = pow(zoom_level/14,2)  # 예시로 줌 레벨에 따른 단순화 비율 설정
        simplify_with_mapshaper(input_file, simplified_file, simplification_ratio)

        tile_size = tile_size_at_zoom(zoom_level)    
        limit_length = tile_size * 0.005
        if zoom_level == max_zoom:
            limit_length = 0
        print(f'zoom : {zoom_level} : {limit_length}')
        # Filter lines by length and save to output_folder
        output_file = os.path.join(output_folder, f"{layer_name}_{zoom_level}.shp")
        filter_lines_by_length(simplified_file, output_file, limit_length)


    print("Shapefiles simplified and dissolved successfully.")


# 실행 부분 ######################

## 포인트

### 포인트는 전처리 없이 저장

In [ ]:
layer_name = "accident"
filename = "A:\\test.tsv"
zoom_level = 14
xcol ="x_crdnt"
ycol = "y_crdnt"
sourceCRS = "EPSG:5179"
MVT_EXTENT = 4096

tiles_data = defaultdict(lambda: defaultdict(lambda: defaultdict(list)))

process_point_layer(layer_name, filename, zoom_level, xcol, ycol,  sourceCRS, MVT_EXTENT, tiles_data)

## 라인 레이어

### 전처리

In [ ]:

input_file = "z:/temp/새 폴더/road.shp"
temp_folder = "z:/temp/새 폴더/temp/"
output_folder = "z:/temp/새 폴더/simplified/"
layer_name = "road"
min_zoom = 6
max_zoom = 14
os.makedirs(output_folder, exist_ok=True)
simplify_linestring(input_file, temp_folder, output_folder, layer_name, min_zoom, max_zoom)


### 타일링

In [ ]:
layer_name = "road"
folder_name = "Z:\\temp\\새 폴더\\simplified"
zoom_levels = range(min_zoom,max_zoom+1)
tiles_data = defaultdict(lambda: defaultdict(lambda: defaultdict(list)))

__MVT_EXTENT = 4096

process_lineString_layer(layer_name, folder_name, zoom_levels, tiles_data, __MVT_EXTENT)

## 건물용

### 폴리곤 줌 레벨에 맞게 단순화 전처리

In [ ]:
layer_name = "building"
input_file = f"z:/temp/새 폴더/{layer_name}.shp"
output_folder = "z:/temp/새 폴더/simplified/"
simplification_ratio_arr = [0.1, 0.1,  0.1, 0.1, 0.1,
                             0.1, 0.1, 0.1, 0.1, 0.1,
                              0.1, 0.1, 0.1, 0.5, 1.0,]
os.makedirs(output_folder, exist_ok=True)


for zoom_level in range(13, 15):
    simplified_file = os.path.join(output_folder, f"{layer_name}_{zoom_level}.shp")
    simplification_ratio = simplification_ratio_arr[zoom_level]  # 예시로 줌 레벨에 따른 단순화 비율 설정
    simplify_with_mapshaper(input_file, simplified_file, simplification_ratio)

print("Shapefiles simplified and dissolved successfully.")

### 건물 타일화

In [ ]:
tiles_data = defaultdict(lambda: defaultdict(lambda: defaultdict(list)))
source_folder = "z:/temp/새 폴더/simplified"

__MVT_EXTENT = 16384

#폴리곤을 포함하면 당연히 주변의 둘레 라인도 그릴 수 있지만
#picking 과 같은 이유 등으로 폴리곤을 제외하고 라인만 그릴 경우에는
#아래 옵션을 조정하면 된다.
isIncludingLines = False
isIncludingPolygon = True

zoom_levels = range(13,15)
process_polygon_layer("building", source_folder, zoom_levels, tiles_data,\
                       __MVT_EXTENT, isIncludingPolygon, False)


## adm

### 줌 레벨에 맞게 단순화 전처리

In [ ]:
### 미리 emd 파일을 베이스로 해서 줌 레벨에 따라 단순화 및 dissolve를 수행하는 코드
### sgg와 sido 단위 역시 emd로부터 만들어냄
### 경계가 잘 맞아야 하기 때문

input_file = "z:/temp/새 폴더/emd.shp"
output_folder = "z:/temp/새 폴더/simplified/"

os.makedirs(output_folder, exist_ok=True)

for zoom_level in range(1, 15):
    simplified_file = os.path.join(output_folder, f"emd_{zoom_level}.shp")
    simplification_ratio = pow(zoom_level/14,2)  # 예시로 줌 레벨에 따른 단순화 비율 설정
    simplify_with_mapshaper(input_file, simplified_file, simplification_ratio)

    # Dissolve by sido, sidonm, sgg, sggnm
    dissolved_file_sgg = os.path.join(output_folder, f"sgg_{zoom_level}.shp")
    dissolve_with_mapshaper(simplified_file, dissolved_file_sgg, ['sidocd', 'sidonm', 'sggcd', 'sggnm'])

    # Dissolve by sido, sidonm
    dissolved_file_sido = os.path.join(output_folder, f"sido_{zoom_level}.shp")
    dissolve_with_mapshaper(dissolved_file_sgg, dissolved_file_sido, ['sidocd', 'sidonm'])

print("Shapefiles simplified and dissolved successfully.")


### adm 타일화

In [ ]:
tiles_data = defaultdict(lambda: defaultdict(lambda: defaultdict(list)))
source_folder = "z:/temp/새 폴더/simplified"

__MVT_EXTENT = 4096

#폴리곤을 포함하면 당연히 주변의 둘레 라인도 그릴 수 있지만
#picking 과 같은 이유 등으로 폴리곤을 제외하고 라인만 그릴 경우에는
#아래 옵션을 조정하면 된다.
isIncludingLines = True
isIncludingPolygon = True

zoom_levels = range(10,15)
process_polygon_layer("emd", source_folder, zoom_levels, tiles_data, __MVT_EXTENT, isIncludingPolygon, isIncludingLines)

zoom_levels = range(7,15)
process_polygon_layer("sgg", source_folder, zoom_levels, tiles_data, __MVT_EXTENT, isIncludingPolygon, isIncludingLines)

zoom_levels = range(1,15)
process_polygon_layer("sido", source_folder, zoom_levels, tiles_data, __MVT_EXTENT, isIncludingPolygon, isIncludingLines)



## 포인트 레이어 저장

In [ ]:
# 타일 데이터 저장
layer_name = "accident"
tile_dir = f"Z:/temp/point/{layer_name}/"
__MVT_EXTENT = 4096

for zoom_level, tiles in tiles_data.items():
    for (x_tile, y_tile), features in tiles.items():
        tile_path = os.path.join(tile_dir, str(zoom_level), str(x_tile))
        os.makedirs(tile_path, exist_ok=True)
        mvt_path = os.path.join(tile_path, f"{y_tile}.mvt")

        all_features = []
        for layer_name, layer_features in features.items():   
            tile_layer = {
                "name": layer_name,
                "features": [{
                    "geometry": feat["geometry"],
                    "properties": feat["properties"]
                } for feat in layer_features]
            }
            all_features.append(tile_layer)

        with open(mvt_path, 'wb') as f:
            f.write(mapbox_vector_tile.encode(all_features, default_options={"extents": __MVT_EXTENT}))

## 라인 레이어 저장

In [ ]:
import os
import mapbox_vector_tile

# 타일 저장 디렉토리 설정
tile_dir = "Z:/temp/map4/"
__MVT_EXTENT = 4096

# 누적된 데이터를 MVT 파일로 저장
for zoom_level, tiles in tiles_data.items():
    for (x_tile, y_tile), features in tiles.items():
        tile_path = os.path.join(tile_dir, str(zoom_level), str(x_tile))
        os.makedirs(tile_path, exist_ok=True)
        mvt_path = os.path.join(tile_path, f"{y_tile}.mvt")

        all_features = []
        for layer_name, layer_features in features.items():        

            tile_layer = {
                "name": layer_name,
                "features": [{
                    "geometry": feat["geometry"],
                    "properties": feat["properties"]
                } for feat in layer_features]
            }
            all_features.append(tile_layer)

        
        with open(mvt_path, 'wb') as f:
            f.write(mapbox_vector_tile.encode(all_features, \
            default_options={"extents":__MVT_EXTENT, "on_invalid_geometry": on_invalid_geometry_make_valid},))


## 폴리곤 레이어 저장

In [ ]:
import os
import mapbox_vector_tile

# 타일 저장 디렉토리 설정
tile_dir = "Z:/temp/building/"
__MVT_EXTENT = 4096

# 누적된 데이터를 MVT 파일로 저장
for zoom_level, tiles in tiles_data.items():
    for (x_tile, y_tile), features in tiles.items():
        tile_path = os.path.join(tile_dir, str(zoom_level), str(x_tile))
        os.makedirs(tile_path, exist_ok=True)
        mvt_path = os.path.join(tile_path, f"{y_tile}.mvt")

        all_features = []
        for layer_name, layer_features in features.items():        

            tile_layer = {
                "name": layer_name,               
                "features": [{
                    #geometry와 properties이외의 필드를 넣으면
                    #mvt의 fields에 추가된다.
                    #"id" : get_layer_value(layer_name),
                    "geometry": feat["geometry"],
                    "properties": ["properties"],
                                } for feat in layer_features]
            }
            all_features.append(tile_layer)

        
        with open(mvt_path, 'wb') as f:
            f.write(mapbox_vector_tile.encode(all_features, \
            default_options={"extents":__MVT_EXTENT,                              
                             "on_invalid_geometry": on_invalid_geometry_make_valid},))


# 여러개의 MVT 폴더들 합치기

In [ ]:
import os
import shutil
import mapbox_vector_tile


def merge(source_paths,  mvt_extent, mvt_version):
    
    featureDic = {}
    for source_path in source_paths:
        with open(source_path, 'rb') as f:
            data = f.read()
        decoded_data = mapbox_vector_tile.decode(data)
        
        for key, value in decoded_data.items():
            if key in featureDic:
                if mvt_extent != value["extent"] or \
                    mvt_version != value["version"]:
                    raise ValueError(f"Error: {key}의 extent 또는 version이 일치하지 않습니다.")
                featureDic[key]["features"].extend(value["features"])
            else:
                # featureDic에 존재하지 않는 key라면 새로운 key로 추가
                featureDic[key] = {
                    "features": value["features"]
                }

    all_features = []


    for layer_name, layer_features in featureDic.items():        
        tile_layer = {
            "name": layer_name,
            "features": [
                         {
                            "geometry": feature["geometry"],
                            "properties": feature["properties"]
                         } for feature in layer_features["features"]
            ]       
        }
        all_features.append(tile_layer)

    return all_features, mvt_extent


def extract_extent_from_first_file(file_dict):
    # 첫 번째 파일 경로 추출
    first_file_key = next(iter(file_dict.keys()))
    first_source_folder = file_dict[first_file_key][0]
    first_file_path = os.path.join(first_source_folder, first_file_key)

    # 파일 열고 extent 추출
    with open(first_file_path, 'rb') as f:
        data = f.read()
    
    decoded_data = mapbox_vector_tile.decode(data)
    
    # 첫 번째 레이어에서 extent 추출
    first_item = next(iter(decoded_data.values()))
    mvt_extent = first_item["extent"]
    mvt_version = first_item["version"]

    return mvt_extent, mvt_version


def merge_mvt_folders(source_folders, target_folder):
    # 딕셔너리 생성
    file_dict = {}
    print("경로 탐색 시작")
    # 모든 source_folders의 z/x/y.mvt 구조를 읽어서 딕셔너리에 저장
    for source_folder in source_folders:
        for root, dirs, files in os.walk(source_folder):
            for file in files:
                if file.endswith(".mvt"):
                    # 경로를 relative_path로 변환
                    relative_path = os.path.relpath(root, source_folder)
                    file_key = os.path.join(relative_path, file)

                    # 딕셔너리에 추가
                    if file_key in file_dict:
                        file_dict[file_key].append(source_folder)
                    else:
                        file_dict[file_key] = [source_folder]

    print("경로 탐색 완료. 병합 시작")
     # 첫 번째 파일에서 extent 추출
    mvt_extent, mvt_version = extract_extent_from_first_file(file_dict)
    print(f"Extracted extent: {mvt_extent}")

    # 타겟 폴더로 파일을 병합 및 복사
    i = 0
    for file_key, source_folders in file_dict.items():
        target_file_path = os.path.join(target_folder, file_key)
        target_file_dir = os.path.dirname(target_file_path)
        
        if (i % 2000 == 0):
            print(f"{i}번째 파일 처리 중")
        i += 1

        # 해당 타겟 경로가 이미 존재하는지 확인
        if os.path.exists(target_file_path):
            # 병합 처리
            source_file_paths = [os.path.join(folder, file_key) for folder in source_folders]
            all_file_paths = source_file_paths + [target_file_path]
            #print(source_file_paths)
            all_features, mvt_extent = merge(all_file_paths,  mvt_extent, mvt_version)
            with open(target_file_path, 'wb') as f:
                f.write(mapbox_vector_tile.encode(all_features, \
                    default_options={"extents": mvt_extent, \
                                    "on_invalid_geometry": on_invalid_geometry_make_valid}))
        else:
            # 폴더가 없으면 생성
            if not os.path.exists(target_file_dir):
                os.makedirs(target_file_dir)
            
            source_file_paths = [os.path.join(folder, file_key) for folder in source_folders]
            # source_file_paths 원소가 하나면 그냥 복사
            # source_file_paths 원소가 여러개면 병합
            if len(source_file_paths) == 1:
                shutil.copyfile(source_file_paths[0], target_file_path)
            else:
                all_features, mvt_extent = merge(source_file_paths,  mvt_extent, mvt_version)
                with open(target_file_path, 'wb') as f:
                    f.write(mapbox_vector_tile.encode(all_features, \
                        default_options={"extents": mvt_extent, \
                                        "on_invalid_geometry": on_invalid_geometry_make_valid}))
        

# <<<<<<  실제 작업  >>>>>>>

## 전국 건물

In [ ]:
source_folder = "X:/202312_전국/전자지도/"
# source_folder의 1차 하위 폴더 읽기
# 1차 하위 폴더의 이름만 변수에 저장. 상위 경로는 제외
sub_folders = [f.name for f in os.scandir(source_folder) if f.is_dir()]


sub_folders

In [ ]:

layer_name = "building"
output_folder = "z:/temp/mapwork/building/"
simplification_ratio_arr = [0.001, 0.005,  0.02, 0.04, 0.05,
                             0.07, 0.1, 0.2, 0.3, 0.4,
                              0.5, 1, 2, 5, 100,]
write_fields = ['BDTYP_CD', 'BD_MGT_SN', 'GRO_FLO_CO']

for sub_folder in sub_folders:
    input_file = os.path.join(source_folder, sub_folder, "TL_SPBD_BULD.shp")
    target_folder = os.path.join(output_folder, sub_folder)
    os.makedirs(target_folder, exist_ok=True)
    print(target_folder)
    for zoom_level in range(1, 13):
        simplified_file = os.path.join(target_folder, f"{layer_name}_{zoom_level}.shp")
        simplification_ratio = 0.01 * simplification_ratio_arr[zoom_level]  # 예시로 줌 레벨에 따른 단순화 비율 설정
        simplify_with_mapshaper(input_file, simplified_file, simplification_ratio,\
                                write_fields, 'cp949', 'utf8')
        print(simplified_file)



print("Shapefiles simplified and dissolved successfully.")

In [ ]:
sub_folders_modify = sub_folders[3:17]
sub_folders_modify

In [ ]:
__MVT_EXTENT = 8192
isIncludingLines = False
isIncludingPolygon = True
source_crs_manual = "+proj=tmerc +lat_0=38 +lon_0=127.5 +k=0.9996 +x_0=1000000 +y_0=2000000 +ellps=GRS80 +towgs84=0,0,0,0,0,0,0 +units=m +no_defs"
output_folder = "z:/temp/mapwork/building/"

tile_folder = "Z:/temp/mapwork/tiles/"
#tile_folder = "Z:/Github/first_map_app/public/buildingWhole/"

for sub_folder in sub_folders_modify:
    
    tiles_data = defaultdict(lambda: defaultdict(lambda: defaultdict(list)))
    source_folder = os.path.join(output_folder, sub_folder)  
    zoom_levels = range(1,13)
    print(source_folder)
    process_polygon_layer("building", source_folder, zoom_levels, tiles_data,\
                        __MVT_EXTENT, isIncludingPolygon, isIncludingLines, source_crs_manual)
    
    tile_dir = os.path.join(tile_folder, sub_folder)
    print("타일링 끝. 저장 시작")
    # 누적된 데이터를 MVT 파일로 저장
    for zoom_level, tiles in tiles_data.items():
        for (x_tile, y_tile), features in tiles.items():
            tile_path = os.path.join(tile_dir, str(zoom_level), str(x_tile))
            os.makedirs(tile_path, exist_ok=True)
            mvt_path = os.path.join(tile_path, f"{y_tile}.mvt")

            all_features = []
            for layer_name, layer_features in features.items():        

                tile_layer = {
                    "name": layer_name,               
                    "features": [{
                        #geometry와 properties이외의 필드를 넣으면
                        #mvt의 fields에 추가된다.
                        #"id" : get_layer_value(layer_name),
                        "geometry": feat["geometry"],
                        "properties": feat["properties"]
                    } for feat in layer_features]
                }
                all_features.append(tile_layer)

            
            with open(mvt_path, 'wb') as f:
                f.write(mapbox_vector_tile.encode(all_features, \
                default_options={"extents":__MVT_EXTENT,\
                                 "y_coord_down" : False,\
                                 "check_winding_order": True,\
                                  "on_invalid_geometry": on_invalid_geometry_make_valid},))

    print("저장 완료")


In [ ]:

# 사용 예시
output_folder = "z:/temp/mapwork/tiles"
# 폴더 내의 모든 폴더 경로를 읽어서 리스트로 저장
source_folders = [f.path for f in os.scandir(output_folder) if f.is_dir()]

target_folder = 'z:/temp/mapwork/merged'

merge_mvt_folders(source_folders, target_folder)